In [ ]:
%matplotlib notebook

In [ ]:
# A bunch of imports we use below
import matplotlib.pyplot as plt

import numpy as np
import numpy.linalg as la

In [ ]:
# Parameters
s = 1.0
beta = 0.5
rho = 0.0001

# Armijo rule
def armijo(f, x, grad, direction):
    m = 0
    while (f(x) - f(x + beta**m * s * direction)) < - rho*s * np.dot(grad,direction):
        m += 1
        if m > 200:
            raise Exception('Unable to find a good step size.')
    return beta**m * s

# Newton's method
def newton(f, grad_f, hessian_f, x_0, tol=1e-4):
    points = [x_0] #We'll store the points in a linked list
    x = x_0
    direction = -la.solve(hessian_f(x), grad_f(x))
    eta = la.norm(direction)
    iters = 0
    
    while eta > tol: #We need some criterion
        step_size = armijo(f, x, grad_f(x), direction)
        
        x = x + step_size * direction #Update point
        points.append(x)

        # Prepare for next iteration
        direction = -la.solve(hessian_f(x), grad_f(x))
        eta = la.norm(direction)
        iters += 1
        if iters > 500:
            raise Exception('Passed maximal iteration count.')
        
    return points

In [ ]:
# Define functions
def f(x):
    return 100 * (x[1] - x[0]**2)**2 + (1 - x[0])**2

def grad_f(x):
    return np.array([400 * x[0]**3 - 400*x[0]*x[1] + 2*x[0] -2,
                     -200 * x[0]**2 + 200 *x[1]])

def hessian_f(x):
    return np.array([[1200 * x[0]**2 - 400*x[1] + 2, -400*x[0]],
                     [-400*x[0], 200]])
    
x_0 = np.array([-2,3], dtype=np.float)

#Run the Newton iteration
points = newton(f, grad_f, hessian_f, x_0)

# Some data for the contour plot
def f_comp(x,y):
    return f(np.array([x,y]))

x = np.linspace(-5,5,num=200)
y = np.linspace(-5,5,num=200)
X, Y = np.meshgrid(x,y)
Z = f_comp(X,Y)

#Finally we'll make the picture
fig, ax = plt.subplots()
ax.contour(X,Y,Z,50)
#We need to split the list of points into x values and y values to plot it
xs = [pt[0] for pt in points]
ys = [pt[1] for pt in points]
ax.plot(xs, ys, '-or')